기존 10000개정도 학습 데이터에서 310000개로 31배 이상 학습 데이터가 늘어났다. 

첫 512 토큰으로 잘라서 ColBERT를 학습했을때 ranking이 얼만큼 좋아졌는지 한번 살펴본다. 

query와 document를 쪼개서 학습하는 방법은 코드를 뜯어고칠게 꽤 많기 때문에 일단 기본적인 truncation 방법 진행후 추가적으로 진행할 예정이다. 

In [1]:
import numpy as np 
import pandas as pd 
import string 
import torch 
import torch.nn as nn 
from transformers import BertPreTrainedModel, BertModel, BertTokenizerFast, AdamW
from colbert.parameters import DEVICE 
import time 
import random 
from colbert.modeling.tokenization import QueryTokenizer, DocTokenizer, tensorize_triples
from colbert.utils.amp import MixedPrecisionManager
from multiprocessing import Pool 
from argparse import ArgumentParser 
from colbert.utils.utils import print_message
from functools import partial


from transformers import AdamW
from colbert.utils.runs import Run
from colbert.utils.amp import MixedPrecisionManager

from colbert.training.lazy_batcher import LazyBatcher
from colbert.training.eager_batcher import EagerBatcher
from colbert.parameters import DEVICE

from colbert.modeling.colbert import ColBERT
from colbert.utils.utils import print_message
from colbert.training.utils import print_progress, manage_checkpoints


import colbert.utils.distributed as distributed

from colbert.utils.parser import Arguments
from colbert.utils.runs import Run
from colbert.training.training import train



In [2]:
!python -m colbert.train --amp --doc_maxlen 512 --query_maxlen 512 \
--mask-punctuation --bsize 8 --accum 4 --triples train_df.tsv

1 False 64


[Dec 06, 08:01:57] #> Creating directory /workspace/patent_similarity/ColBERT/experiments/dirty/train.py/2021-12-06_08.01.48 




[Dec 06, 08:01:57] #> Creating directory /workspace/patent_similarity/ColBERT/experiments/dirty/train.py/2021-12-06_08.01.48/logs/ 


[Dec 06, 08:01:57] {'root': 'experiments', 'experiment': 'dirty', 'run': '2021-12-06_08.01.48', 'rank': -1, 'similarity': 'cosine', 'dim': 128, 'query_maxlen': 512, 'doc_maxlen': 512, 'mask_punctuation': True, 'resume': False, 'resume_optimizer': False, 'checkpoint': None, 'lr': 3e-06, 'maxsteps': 400000, 'bsize': 8, 'accumsteps': 4, 'amp': True, 'triples': 'train_df.tsv', 'queries': None, 'collection': None} 

1
===== Executing Eager Batching =====
Some weights of the model checkpoint at bert-base-uncased were not used when initializing ColBERT: ['cls.predictions.bias', 'cls.predictions.transform.dense.weight', 'cls.predictions.transform.dense.bias', 'cls.predictions.decoder.weight', 'cls.seq_relationship.weight'

[Dec 06, 08:02:39] 28 0.9895393655689934
#>>>    342.39 317.77 		|		 24.620000000000005
#>>>    336.69 308.08 		|		 28.610000000000014
#>>>    344.63 322.62 		|		 22.00999999999999
#>>>    366.94 315.84 		|		 51.10000000000002
[Dec 06, 08:02:40] 29 0.9565547528324709
#>>>    329.78 306.72 		|		 23.059999999999945
#>>>    337.42 307.09 		|		 30.33000000000004
#>>>    335.39 319.59 		|		 15.800000000000011
#>>>    361.19 320.44 		|		 40.75
[Dec 06, 08:02:40] 30 0.9338138682457401
#>>>    351.97 296.84 		|		 55.13000000000005
#>>>    319.14 311.92 		|		 7.21999999999997
#>>>    336.1 305.03 		|		 31.07000000000005
#>>>    339.85 318.92 		|		 20.930000000000007
[Dec 06, 08:02:41] 31 0.9046531237236617
#>>>    338.8 315.55 		|		 23.25
#>>>    325.58 322.46 		|		 3.1200000000000045
#>>>    340.33 324.77 		|		 15.560000000000002
#>>>    338.16 301.96 		|		 36.200000000000045
[Dec 06, 08:02:42] 32 0.8949128363659357
#>>>    333.41 310.59 		|		 22.82000000000005
#>>>    344.68 310.98 		|		 33.6

[Dec 06, 08:03:04] 65 0.717955925909327
#>>>    353.18 317.62 		|		 35.56
#>>>    360.27 330.5 		|		 29.769999999999982
#>>>    370.41 287.26 		|		 83.15000000000003
#>>>    342.23 283.37 		|		 58.860000000000014
[Dec 06, 08:03:05] 66 0.707240165821128
#>>>    349.96 314.73 		|		 35.22999999999996
#>>>    331.62 319.86 		|		 11.759999999999991
#>>>    341.17 288.62 		|		 52.55000000000001
#>>>    362.84 325.38 		|		 37.45999999999998
[Dec 06, 08:03:05] 67 0.7357547004580376
#>>>    350.35 307.8 		|		 42.55000000000001
#>>>    345.19 322.66 		|		 22.529999999999973
#>>>    358.58 335.53 		|		 23.05000000000001
#>>>    383.59 352.59 		|		 31.0
[Dec 06, 08:03:06] 68 0.7250916825818843
#>>>    323.67 322.33 		|		 1.3400000000000318
#>>>    355.08 330.59 		|		 24.49000000000001
#>>>    359.86 285.58 		|		 74.28000000000003
#>>>    359.95 304.36 		|		 55.589999999999975
[Dec 06, 08:03:07] 69 0.7402856002663715
#>>>    373.04 312.37 		|		 60.670000000000016
#>>>    344.69 318.02 		|		 26.6700

#>>>    355.17 333.51 		|		 21.660000000000025
#>>>    362.12 336.54 		|		 25.579999999999984
#>>>    365.52 339.88 		|		 25.639999999999986
#>>>    366.65 329.67 		|		 36.97999999999996
[Dec 06, 08:03:30] 103 0.771486994843623
#>>>    386.11 341.71 		|		 44.400000000000034
#>>>    354.38 344.88 		|		 9.5
#>>>    360.51 310.42 		|		 50.089999999999975
#>>>    380.93 325.37 		|		 55.56
[Dec 06, 08:03:31] 104 0.7641400765512139
#>>>    353.49 316.04 		|		 37.44999999999999
#>>>    367.62 338.24 		|		 29.379999999999995
#>>>    360.58 346.5 		|		 14.079999999999984
#>>>    360.22 335.68 		|		 24.54000000000002
[Dec 06, 08:03:31] 105 0.7569564867772224
#>>>    356.46 346.34 		|		 10.120000000000005
#>>>    367.23 334.53 		|		 32.700000000000045
#>>>    361.75 325.18 		|		 36.56999999999999
#>>>    359.23 325.36 		|		 33.870000000000005
[Dec 06, 08:03:32] 106 0.7499566247293766
#>>>    368.93 322.55 		|		 46.379999999999995
#>>>    349.12 338.18 		|		 10.939999999999998
#>>>    351.75 325.5

#>>>    372.96 331.62 		|		 41.339999999999975
#>>>    361.05 341.64 		|		 19.410000000000025
#>>>    360.56 333.95 		|		 26.610000000000014
#>>>    366.44 334.56 		|		 31.879999999999995
[Dec 06, 08:03:55] 140 0.7194228032089481
#>>>    367.14 342.48 		|		 24.659999999999968
#>>>    378.62 345.92 		|		 32.69999999999999
#>>>    370.78 309.96 		|		 60.81999999999999
#>>>    375.38 349.53 		|		 25.850000000000023
[Dec 06, 08:03:56] 141 0.7143564456497465
#>>>    377.77 354.32 		|		 23.44999999999999
#>>>    357.68 327.22 		|		 30.45999999999998
#>>>    368.07 331.18 		|		 36.889999999999986
#>>>    371.95 351.86 		|		 20.089999999999975
[Dec 06, 08:03:56] 142 0.7093609537408753
#>>>    346.52 331.91 		|		 14.609999999999957
#>>>    368.55 363.49 		|		 5.060000000000002
#>>>    364.57 321.61 		|		 42.95999999999998
#>>>    385.61 354.23 		|		 31.379999999999995
[Dec 06, 08:03:57] 143 0.7044534483814038
#>>>    372.31 349.45 		|		 22.860000000000014
#>>>    396.86 350.89 		|		 45.97000000

...

#>>>    467.54 449.7 		|		 17.840000000000032
#>>>    476.87 454.35 		|		 22.519999999999982
#>>>    466.54 448.87 		|		 17.670000000000016
[Dec 06, 15:11:55] 38786 0.13037746564746608
#>>>    469.31 449.71 		|		 19.600000000000023
#>>>    467.87 456.72 		|		 11.149999999999977
#>>>    457.95 451.54 		|		 6.409999999999968
#>>>    461.34 449.3 		|		 12.039999999999964
[Dec 06, 15:11:55] 38787 0.13037411947083696
#>>>    464.53 445.3 		|		 19.22999999999996
#>>>    464.72 446.86 		|		 17.860000000000014
#>>>    476.65 455.67 		|		 20.97999999999996
#>>>    466.1 448.59 		|		 17.510000000000048
[Dec 06, 15:11:56] 38788 0.13037076093588554
#>>>    474.74 463.29 		|		 11.449999999999989
#>>>    476.38 459.89 		|		 16.49000000000001
#>>>    466.94 449.64 		|		 17.30000000000001
#>>>    467.52 450.66 		|		 16.859999999999957
[Dec 06, 15:11:56] 38789 0.13036740026048924
#>>>    471.27 445.38 		|		 25.889999999999986
#>>>    467.9 456.14 		|		 11.759999999999991
#>>>    472.97 458.83 		|		 14.

#>>>    472.02 452.48 		|		 19.539999999999964
#>>>    469.71 452.06 		|		 17.649999999999977
[Dec 06, 15:12:21] 38821 0.13037630842450174
#>>>    466.34 455.07 		|		 11.269999999999982
#>>>    469.95 452.13 		|		 17.819999999999993
#>>>    470.14 456.22 		|		 13.919999999999959
#>>>    470.06 453.66 		|		 16.399999999999977
[Dec 06, 15:12:21] 38822 0.13037295048508984
#>>>    471.77 454.66 		|		 17.109999999999957
#>>>    475.99 455.23 		|		 20.75999999999999
#>>>    472.23 456.35 		|		 15.879999999999995
#>>>    473.44 452.49 		|		 20.94999999999999
[Dec 06, 15:12:22] 38823 0.13036959244232088
#>>>    465.91 452.21 		|		 13.700000000000045
#>>>    471.01 461.29 		|		 9.71999999999997
#>>>    466.34 450.63 		|		 15.70999999999998
#>>>    467.18 456.88 		|		 10.300000000000011
[Dec 06, 15:12:23] 38824 0.13036631274736105
#>>>    473.21 458.59 		|		 14.620000000000005
#>>>    468.66 452.27 		|		 16.390000000000043
#>>>    466.26 459.29 		|		 6.96999999999997
#>>>    464.29 451.79 		|		 

#>>>    469.44 453.08 		|		 16.360000000000014
#>>>    469.63 450.82 		|		 18.810000000000002
[Dec 06, 15:12:43] 38857 0.13036438643079418
#>>>    470.79 452.79 		|		 18.0
#>>>    471.68 455.11 		|		 16.569999999999993
#>>>    470.01 454.42 		|		 15.589999999999975
#>>>    457.72 453.16 		|		 4.560000000000002
[Dec 06, 15:12:44] 38858 0.1303634390419388
#>>>    473.15 452.63 		|		 20.519999999999982
#>>>    475.81 457.68 		|		 18.129999999999995
#>>>    476.47 459.07 		|		 17.400000000000034
#>>>    476.76 460.01 		|		 16.75
[Dec 06, 15:12:45] 38859 0.1303600843613495
#>>>    459.22 458.26 		|		 0.9600000000000364
#>>>    471.17 451.75 		|		 19.420000000000016
#>>>    473.65 457.59 		|		 16.060000000000002
#>>>    473.65 456.23 		|		 17.41999999999996
[Dec 06, 15:12:45] 38860 0.13037596023963668
#>>>    465.26 452.47 		|		 12.789999999999964
#>>>    467.06 456.27 		|		 10.79000000000002
#>>>    467.09 454.88 		|		 12.20999999999998
#>>>    465.5 454.17 		|		 11.329999999999984
[Dec 06,

#>>>    471.28 456.3 		|		 14.979999999999961
[Dec 06, 15:13:06] 38893 0.13034923471872667
#>>>    474.63 460.36 		|		 14.269999999999982
#>>>    467.7 452.95 		|		 14.75
#>>>    464.32 452.09 		|		 12.230000000000018
#>>>    472.14 465.85 		|		 6.289999999999964
[Dec 06, 15:13:07] 38894 0.13034629064705225
#>>>    463.53 458.49 		|		 5.039999999999964
#>>>    463.7 447.01 		|		 16.689999999999998
#>>>    465.91 461.44 		|		 4.470000000000027
#>>>    466.61 452.1 		|		 14.509999999999991
[Dec 06, 15:13:08] 38895 0.13035481274990288
#>>>    472.59 454.14 		|		 18.44999999999999
#>>>    466.07 449.98 		|		 16.089999999999975
#>>>    470.26 454.62 		|		 15.639999999999986
#>>>    468.47 456.38 		|		 12.090000000000032
[Dec 06, 15:13:08] 38896 0.1303514626447373
#>>>    467.69 452.75 		|		 14.939999999999998
#>>>    469.1 458.47 		|		 10.629999999999995
#>>>    464.23 448.88 		|		 15.350000000000023
#>>>    469.17 453.25 		|		 15.920000000000016
[Dec 06, 15:13:09] 38897 0.13035003287882255

[Dec 06, 15:13:29] 38929 0.13029587204067117
#>>>    466.19 455.94 		|		 10.25
#>>>    460.39 448.79 		|		 11.599999999999966
#>>>    465.75 457.02 		|		 8.730000000000018
#>>>    469.33 453.37 		|		 15.95999999999998
[Dec 06, 15:13:30] 38930 0.1302937904021011
#>>>    468.36 445.99 		|		 22.370000000000005
#>>>    468.88 453.16 		|		 15.71999999999997
#>>>    472.13 453.31 		|		 18.819999999999993
#>>>    464.44 449.83 		|		 14.610000000000014
[Dec 06, 15:13:31] 38931 0.13029044389369035
